

# 最良のトライアルの再利用

ハイパーパラメータ最適化後に、最良のハイパーパラメータで再度目的関数を評価したい場合があります。

例えば、

- Optunaで最適なハイパーパラメータを見つけ、これまでに見つかった最良のハイパーパラメータを使用して同様の `objective` 関数を実行し、結果をさらに分析したい場合や、
- トレーニング時間を短縮するために部分データセットでOptunaを使用して最適化を行った後、最良のハイパーパラメータ値を使用して全データセットでモデルをトレーニングしたい場合

:class:`~optuna.study.Study.best_trial` は、現在の最良のハイパーパラメータ値で目的関数を再評価するためのインターフェースを提供します。

このチュートリアルでは、上記の最初の例のように、現在の最良の値を使用して異なる `objective` 関数を再実行する例を示します。


## 最良のモデルの詳細調査

Optunaを使用して古典的な教師あり分類問題を考えてみましょう：


In [ ]:
from sklearn import metrics
from sklearn.datasets import make_classification
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split


import optuna


def objective(trial):
    X, y = make_classification(n_features=10, random_state=1)
    X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1)

    C = trial.suggest_float("C", 1e-7, 10.0, log=True)

    clf = LogisticRegression(C=C)
    clf.fit(X_train, y_train)

    return clf.score(X_test, y_test)


study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=10)

print(study.best_trial.value)  # 最良の値を表示します。

ハイパーパラメータ最適化後、同じデータセットで再現率、適合率、F1スコアなどの他の評価指標を計算したい場合
最良のハイパーパラメータでモデルを再現するために、 ``objective`` 関数の大部分を共有する別の目的関数を定義できます。



In [ ]:
def detailed_objective(trial):
    # 最良のモデルを再現するためのobjective関数と同じコードを使用
    X, y = make_classification(n_features=10, random_state=1)
    X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1)

    C = trial.suggest_float("C", 1e-7, 10.0, log=True)

    clf = LogisticRegression(C=C)
    clf.fit(X_train, y_train)

    # より詳細な評価指標を計算
    pred = clf.predict(X_test)

    acc = metrics.accuracy_score(pred, y_test)
    recall = metrics.recall_score(pred, y_test)
    precision = metrics.precision_score(pred, y_test)
    f1 = metrics.f1_score(pred, y_test)

    return acc, f1, recall, precision

``study.best_trial`` を ``detailed_objective`` の引数として渡します。



In [ ]:
detailed_objective(study.best_trial)  # acc, f1, recall, precisionを計算

## :class:`~optuna.study.Study.best_trial` と通常のトライアルの違い

この例では :class:`~optuna.study.Study.best_trial` を使用しており、
これは `best_trial` を :class:`~optuna.trial.FrozenTrial` として返します。
:class:`~optuna.trial.FrozenTrial` はアクティブなトライアルとは異なり、
特定の状況では :class:`~optuna.trial.Trial` とは異なる動作をします。
例えば、 :class:`~optuna.trial.FrozenTrial.should_prune` は常に ``False`` を返すため、
プルーニングは機能しません。

<div class="alert alert-info"><h4>Note</h4><p>`multi_objective` で示されているような多目的最適化の場合、
    :attr:`~optuna.study.Study.best_trials` はパレートフロント上の
    :class:`~optuna.trial.FrozenTrial` のリストを返します。
    したがって、上記と同様の方法でリスト内の各トライアルを再利用できます。</p></div>

